In [1]:
def recall(feature_vectors, feature_labels, rank,test_img_list, gallery_vectors=None, gallery_labels=None):
    num_features = len(feature_labels)
    feature_labels = torch.tensor(feature_labels, device=feature_vectors.device)
    gallery_vectors = feature_vectors if gallery_vectors is None else gallery_vectors

    dist_matrix = torch.cdist(feature_vectors.unsqueeze(0), gallery_vectors.unsqueeze(0)).squeeze(0)
    
    if gallery_labels is None:
        dist_matrix.fill_diagonal_(float('inf'))
        gallery_labels = feature_labels
    else:
        gallery_labels = torch.tensor(gallery_labels, device=feature_vectors.device)

    idx = dist_matrix.topk(k=rank[-1], dim=-1, largest=False)[1]
    acc_list = []
    for r in rank:
        correct = (gallery_labels[idx[:, 0:r]] == feature_labels.unsqueeze(dim=-1)).any(dim=-1).float()
        acc_list.append((torch.sum(correct) / num_features).item())
    return acc_list


In [2]:
def test(net, recall_ids):
    net.eval()
    with torch.no_grad():
        # obtain feature vectors for all data
        for key in eval_dict.keys():
            eval_dict[key]['features'] = []
            imgList=[]
            # for inputs, labels in tqdm(eval_dict[key]['data_loader'], desc='processing {} data'.format(key)):
            print('processing {} data'.format(key))
            for batch_idx, (inputs, labels, imgs) in enumerate(eval_dict[key]['data_loader']):
                inputs, labels = inputs.cuda(), labels.cuda()
                features, classes = net(inputs)
                eval_dict[key]['features'].append(features)
                imgList+=imgs
            eval_dict[key]['features'] = torch.cat(eval_dict[key]['features'], dim=0)

        # compute recall metric
        if data_name == 'isc':
            acc_list = recall(eval_dict['test']['features'], test_data_set.label_list, recall_ids,imgList,
                              eval_dict['gallery']['features'], gallery_data_set.label_list)
        else:
            acc_list = recall(eval_dict['test']['features'], test_data_set.label_list, recall_ids,imgList)
    
    desc = 'Test Epoch {}/{} '.format(epoch, num_epochs)
    for index, rank_id in enumerate(recall_ids):
        desc += 'R@{}:{:.2f}% '.format(rank_id, acc_list[index] * 100)
        results['test_recall@{}'.format(rank_id)].append(acc_list[index] * 100)
    print(desc)
    return acc_list[0]


In [3]:
import argparse

import pandas as pd
import torch
from thop import profile, clever_format
from torch.optim import Adam
from torch.optim.lr_scheduler import MultiStepLR
from torch.utils.data import DataLoader
from tqdm import tqdm
from dataset import SingleData
from model import Model, set_bn_eval
from utils import  LabelSmoothingCrossEntropyLoss, BatchHardTripletLoss, ImageReader, MPerClassSampler
import numpy as np
import os
import math 
import torchvision.transforms as transforms

def get_data_list(data_path, ratio=0.001):
    img_list = []
    for root, dirs, files in os.walk(data_path):
        if files == []:
            class_name = dirs
        elif dirs == []:
            for f in files:
                img_path = os.path.join(root, f)
                img_list.append(img_path)

    np.random.seed(1)
    train_img_list = np.random.choice(img_list, size=int(len(img_list)*(1-ratio)), replace=False)
    #print(img_list, train_img_list)
    eval_img_list = list(set(img_list) - set(train_img_list))
    ########add
    half=math.floor(len(eval_img_list)/2)
    print(half)
    eval_=eval_img_list[:half]
    test_=eval_img_list[half:]
    #######
    #return class_name, train_img_list, eval_img_list 
    return class_name, train_img_list


def train(net, optim):
    net.train()
    # fix bn on backbone network
    net.apply(set_bn_eval)
    # total_loss, total_correct, total_num, data_bar = 0, 0, 0, tqdm(train_data_loader)
    print("start")
    total_loss, total_correct, total_num, data_bar = 0, 0, 0, enumerate(train_data_loader)
    print("end")
    # for inputs, labels in data_bar:
    for batch_idx, (inputs, labels, _) in data_bar:
        print(batch_idx)
        inputs, labels = inputs.cuda(), labels.cuda()
        features, classes = net(inputs)
        class_loss = class_criterion(classes, labels)
        feature_loss = feature_criterion(features, labels)
        loss = class_loss + feature_loss
        optim.zero_grad()
        loss.backward()
        optim.step()
        pred = torch.argmax(classes, dim=-1)
        total_loss += loss.item() * inputs.size(0)
        total_correct += torch.sum(pred == labels).item()
        total_num += inputs.size(0)
        print('Train Epoch {}/{} - Loss:{:.4f} - Acc:{:.2f}%'.format(epoch, num_epochs, total_loss / total_num, total_correct / total_num * 100))
        # data_bar.set_description('Train Epoch {}/{} - Loss:{:.4f} - Acc:{:.2f}%'
        #                          .format(epoch, num_epochs, total_loss / total_num, total_correct / total_num * 100))

    return total_loss / total_num, total_correct / total_num * 100




if __name__ == '__main__':
    
    
    # parser = argparse.ArgumentParser(description='Train CGD')
    # parser.add_argument('--data_path', default='/home/data', type=str, help='datasets path')
    # parser.add_argument('--data_name', default='car', type=str, choices=['car', 'cub', 'sop', 'isc'],
    #                     help='dataset name')
    # parser.add_argument('--crop_type', default='uncropped', type=str, choices=['uncropped', 'cropped'],
    #                     help='crop data or not, it only works for car or cub dataset')
    # parser.add_argument('--backbone_type', default='resnet50', type=str, choices=['resnet50', 'resnext50'],
    #                     help='backbone network type')
    # parser.add_argument('--gd_config', default='SG', type=str,
    #                     choices=['S', 'M', 'G', 'SM', 'MS', 'SG', 'GS', 'MG', 'GM', 'SMG', 'MSG', 'GSM'],
    #                     help='global descriptors config')
    # parser.add_argument('--feature_dim', default=1536, type=int, help='feature dim')
    # parser.add_argument('--smoothing', default=0.1, type=float, help='smoothing value for label smoothing')
    # parser.add_argument('--temperature', default=0.5, type=float,
    #                     help='temperature scaling used in softmax cross-entropy loss')
    # parser.add_argument('--margin', default=0.1, type=float, help='margin of m for triplet loss')
    # parser.add_argument('--recalls', default='1,2,4,8', type=str, help='selected recall')
    # parser.add_argument('--batch_size', default=128, type=int, help='train batch size')
    # parser.add_argument('--num_epochs', default=20, type=int, help='train epoch number')

    # opt = parser.parse_args()
    # args parse
    data_path="D:\\original_images_5\\few-person\\for colab\\train"
    # data_path="D:\\models\\CGD-master\\dataset\\img"
    test_path="D:\\original_images_5\\few-person\\for colab\\val"
    data_name="CRC"
    crop_type="uncropped"
    backbone_type="resnet50"
    gd_config="GS"
    feature_dim=1536
    smoothing=0.1
    temperature=0.5
    margin=0.1
    tempRecall='1,2,4,8'
    recalls=[int(k) for k in tempRecall.split(',')]
    batch_size=8
    num_epochs=50
    
    class_name, train_img_list = get_data_list(data_path)
    class_test_name, test_img_list = get_data_list(test_path)
    
    train_transform = transforms.Compose([ 
    transforms.RandomHorizontalFlip(),
    transforms.RandomVerticalFlip(),
    transforms.RandomCrop(224),
    transforms.ToTensor()
])
    
    
    # data_path, data_name, crop_type, backbone_type = opt.data_path, opt.data_name, opt.crop_type, opt.backbone_type
    # gd_config, feature_dim, smoothing, temperature = opt.gd_config, opt.feature_dim, opt.smoothing, opt.temperature
    # margin, recalls, batch_size = opt.margin, [int(k) for k in opt.recalls.split(',')], opt.batch_size
    # num_epochs = opt.num_epochs
    save_name_pre = '{}_{}_{}_{}_{}_{}_{}_{}_{}_gs_pretrian'.format(data_name, crop_type, backbone_type, gd_config, feature_dim,
                                                        smoothing, temperature, margin, batch_size)

    results = {'train_loss': [], 'train_accuracy': []}
#     resultsWithC = {'train_loss': [], 'train_accuracy': []}
    
    for recall_id in recalls:
        results['test_recall@{}'.format(recall_id)] = []
#         resultsWithC['test_recall@{}'.format(recall_id)] = []
        

    train_data_set=SingleData(class_name, train_img_list, train_transform)
    # dataset loader
    # train_data_set = ImageReader(data_path, data_name, 'train', crop_type)
    # train_sample = MPerClassSampler(train_data_set.labels, batch_size)
    train_sample = MPerClassSampler(train_data_set.label_list, batch_size)
    train_data_loader = DataLoader(train_data_set, batch_sampler=train_sample, num_workers=8)
    # test_data_set = ImageReader(data_path, data_name, 'query' if data_name == 'isc' else 'test', crop_type)
    test_data_set = SingleData(class_test_name, test_img_list, train_transform)
    test_data_loader = DataLoader(test_data_set, batch_size, shuffle=False, num_workers=8)
    eval_dict = {'test': {'data_loader': test_data_loader}}
    if data_name == 'isc':
        gallery_data_set = ImageReader(data_path, data_name, 'gallery', crop_type)
        gallery_data_loader = DataLoader(gallery_data_set, batch_size, shuffle=False, num_workers=8)
        eval_dict['gallery'] = {'data_loader': gallery_data_loader}

    # model setup, model profile, optimizer config and loss definition
    model = Model(backbone_type, gd_config, feature_dim, num_classes=3).cuda()
    # model.load_state_dict(torch.load('D:\\models\\CGD-master_2\\CGD-master\\isc_uncropped_resnet50_GS_1536_0.1_0.5_0.1_128_model.pth'))

    flops, params = profile(model, inputs=(torch.randn(1, 3, 224, 224).cuda(),))
    flops, params = clever_format([flops, params])
    print('# Model Params: {} FLOPs: {}'.format(params, flops))
    optimizer = Adam(model.parameters(), lr=1e-4)
    lr_scheduler = MultiStepLR(optimizer, milestones=[int(0.6 * num_epochs), int(0.8 * num_epochs)], gamma=0.1)
    class_criterion = LabelSmoothingCrossEntropyLoss(smoothing=smoothing, temperature=temperature)
    feature_criterion = BatchHardTripletLoss(margin=margin)

    best_recall = 0.0
    for epoch in range(1, num_epochs + 1):
        train_loss, train_accuracy = train(model, optimizer)
        results['train_loss'].append(train_loss)
        results['train_accuracy'].append(train_accuracy)
#         resultsWithC['train_loss'].append(train_loss)
#         resultsWithC['train_accuracy'].append(train_accuracy)
        rank = test(model, recalls)
#         rank2 = testWithTask(model, recalls)
        
        lr_scheduler.step()

        # save statistics
        data_frame = pd.DataFrame(data=results, index=range(1, epoch + 1))
#         data_frame_with_condition = pd.DataFrame(data=resultsWithC, index=range(1, epoch + 1))
        
        data_frame.to_csv('results/{}_statistics.csv'.format(save_name_pre), index_label='epoch')
#         data_frame_with_condition.to_csv('results/{}_statistics_with_condition.csv'.format(save_name_pre), index_label='epoch')
        
        # save database and model
        data_base = {}
        if rank > best_recall:
            best_recall = rank
            data_base['test_images'] = test_data_set.img_list
            data_base['test_labels'] = test_data_set.label_list
            data_base['test_features'] = eval_dict['test']['features']
            if data_name == 'isc':
                data_base['gallery_images'] = gallery_data_set.img_list
                data_base['gallery_labels'] = gallery_data_set.label_list
                data_base['gallery_features'] = eval_dict['gallery']['features']
            torch.save(model.state_dict(), 'results/{}_{}_model.pth'.format(save_name_pre,epoch))
            torch.save(data_base, 'results/{}_{}_data_base.pth'.format(save_name_pre,epoch))


C:\Users\Reza\anaconda3\lib\site-packages\torchvision\io\image.py:11: UserWarning: Failed to load image Python extension: Could not find module 'C:\Users\Reza\anaconda3\Lib\site-packages\torchvision\image.pyd' (or one of its dependencies). Try using the full path with constructor syntax.
  warn(f"Failed to load image Python extension: {e}")


5
0
['s1', 's2', 's3']
['s1', 's2', 's3']
[INFO] Register count_convNd() for <class 'torch.nn.modules.conv.Conv2d'>.
[INFO] Register count_bn() for <class 'torch.nn.modules.batchnorm.BatchNorm2d'>.
[INFO] Register zero_ops() for <class 'torch.nn.modules.activation.ReLU'>.
[INFO] Register zero_ops() for <class 'torch.nn.modules.pooling.MaxPool2d'>.
[WARN] Cannot find rule for <class 'torch.nn.modules.container.Sequential'>. Treat it as zero Macs and zero Params.
[WARN] Cannot find rule for <class 'resnet.Bottleneck'>. Treat it as zero Macs and zero Params.
[WARN] Cannot find rule for <class 'model.GlobalDescriptor'>. Treat it as zero Macs and zero Params.
[WARN] Cannot find rule for <class 'torch.nn.modules.container.ModuleList'>. Treat it as zero Macs and zero Params.
[INFO] Register count_linear() for <class 'torch.nn.modules.linear.Linear'>.
[WARN] Cannot find rule for <class 'model.L2Norm'>. Treat it as zero Macs and zero Params.
[INFO] Register count_bn() for <class 'torch.nn.modul

Train Epoch 1/50 - Loss:1.2237 - Acc:50.00%
149
Train Epoch 1/50 - Loss:1.2219 - Acc:50.25%
150
Train Epoch 1/50 - Loss:1.2209 - Acc:50.25%
151
Train Epoch 1/50 - Loss:1.2192 - Acc:50.41%
152
Train Epoch 1/50 - Loss:1.2228 - Acc:50.08%
153
Train Epoch 1/50 - Loss:1.2231 - Acc:50.08%
154
Train Epoch 1/50 - Loss:1.2231 - Acc:50.08%
155
Train Epoch 1/50 - Loss:1.2209 - Acc:50.24%
156
Train Epoch 1/50 - Loss:1.2195 - Acc:50.40%
157
Train Epoch 1/50 - Loss:1.2207 - Acc:50.40%
158
Train Epoch 1/50 - Loss:1.2223 - Acc:50.39%
159
Train Epoch 1/50 - Loss:1.2233 - Acc:50.31%
160
Train Epoch 1/50 - Loss:1.2236 - Acc:50.31%
161
Train Epoch 1/50 - Loss:1.2229 - Acc:50.31%
162
Train Epoch 1/50 - Loss:1.2223 - Acc:50.31%
163
Train Epoch 1/50 - Loss:1.2217 - Acc:50.30%
164
Train Epoch 1/50 - Loss:1.2216 - Acc:50.08%
165
Train Epoch 1/50 - Loss:1.2211 - Acc:50.08%
166
Train Epoch 1/50 - Loss:1.2209 - Acc:49.93%
167
Train Epoch 1/50 - Loss:1.2205 - Acc:49.93%
168
Train Epoch 1/50 - Loss:1.2202 - Acc:49.

Train Epoch 1/50 - Loss:1.1558 - Acc:53.01%
320
Train Epoch 1/50 - Loss:1.1552 - Acc:53.04%
321
Train Epoch 1/50 - Loss:1.1544 - Acc:53.07%
322
Train Epoch 1/50 - Loss:1.1543 - Acc:53.06%
323
Train Epoch 1/50 - Loss:1.1545 - Acc:53.01%
324
Train Epoch 1/50 - Loss:1.1539 - Acc:53.12%
325
Train Epoch 1/50 - Loss:1.1543 - Acc:53.07%
326
Train Epoch 1/50 - Loss:1.1541 - Acc:53.10%
327
Train Epoch 1/50 - Loss:1.1537 - Acc:53.09%
328
Train Epoch 1/50 - Loss:1.1535 - Acc:53.15%
329
Train Epoch 1/50 - Loss:1.1529 - Acc:53.18%
330
Train Epoch 1/50 - Loss:1.1523 - Acc:53.25%
331
Train Epoch 1/50 - Loss:1.1527 - Acc:53.20%
332
Train Epoch 1/50 - Loss:1.1528 - Acc:53.19%
333
Train Epoch 1/50 - Loss:1.1528 - Acc:53.18%
334
Train Epoch 1/50 - Loss:1.1523 - Acc:53.25%
335
Train Epoch 1/50 - Loss:1.1518 - Acc:53.31%
336
Train Epoch 1/50 - Loss:1.1513 - Acc:53.34%
337
Train Epoch 1/50 - Loss:1.1511 - Acc:53.37%
338
Train Epoch 1/50 - Loss:1.1505 - Acc:53.43%
339
Train Epoch 1/50 - Loss:1.1500 - Acc:53.

Train Epoch 1/50 - Loss:1.1259 - Acc:55.19%
491
Train Epoch 1/50 - Loss:1.1256 - Acc:55.21%
492
Train Epoch 1/50 - Loss:1.1250 - Acc:55.20%
493
Train Epoch 1/50 - Loss:1.1248 - Acc:55.19%
494
Train Epoch 1/50 - Loss:1.1245 - Acc:55.20%
495
Train Epoch 1/50 - Loss:1.1249 - Acc:55.14%
496
Train Epoch 1/50 - Loss:1.1242 - Acc:55.21%
497
Train Epoch 1/50 - Loss:1.1239 - Acc:55.22%
498
Train Epoch 1/50 - Loss:1.1235 - Acc:55.24%
499
Train Epoch 1/50 - Loss:1.1239 - Acc:55.23%
500
Train Epoch 1/50 - Loss:1.1231 - Acc:55.31%
501
Train Epoch 1/50 - Loss:1.1226 - Acc:55.33%
502
Train Epoch 1/50 - Loss:1.1226 - Acc:55.34%
503
Train Epoch 1/50 - Loss:1.1228 - Acc:55.38%
504
Train Epoch 1/50 - Loss:1.1234 - Acc:55.35%
505
Train Epoch 1/50 - Loss:1.1240 - Acc:55.29%
506
Train Epoch 1/50 - Loss:1.1234 - Acc:55.33%
507
Train Epoch 1/50 - Loss:1.1232 - Acc:55.31%
508
Train Epoch 1/50 - Loss:1.1232 - Acc:55.35%
509
Train Epoch 1/50 - Loss:1.1227 - Acc:55.39%
510
Train Epoch 1/50 - Loss:1.1223 - Acc:55.

...

Train Epoch 50/50 - Loss:0.5088 - Acc:97.30%
519
Train Epoch 50/50 - Loss:0.5088 - Acc:97.31%
520
Train Epoch 50/50 - Loss:0.5087 - Acc:97.31%
521
Train Epoch 50/50 - Loss:0.5087 - Acc:97.32%
522
Train Epoch 50/50 - Loss:0.5087 - Acc:97.32%
523
Train Epoch 50/50 - Loss:0.5086 - Acc:97.33%
524
Train Epoch 50/50 - Loss:0.5087 - Acc:97.31%
525
Train Epoch 50/50 - Loss:0.5092 - Acc:97.27%
526
Train Epoch 50/50 - Loss:0.5093 - Acc:97.27%
527
Train Epoch 50/50 - Loss:0.5093 - Acc:97.28%
528
Train Epoch 50/50 - Loss:0.5094 - Acc:97.28%
529
Train Epoch 50/50 - Loss:0.5093 - Acc:97.29%
530
Train Epoch 50/50 - Loss:0.5092 - Acc:97.29%
531
Train Epoch 50/50 - Loss:0.5091 - Acc:97.30%
532
Train Epoch 50/50 - Loss:0.5094 - Acc:97.28%
533
Train Epoch 50/50 - Loss:0.5093 - Acc:97.28%
534
Train Epoch 50/50 - Loss:0.5093 - Acc:97.29%
535
Train Epoch 50/50 - Loss:0.5094 - Acc:97.29%
536
Train Epoch 50/50 - Loss:0.5093 - Acc:97.30%
537
Train Epoch 50/50 - Loss:0.5092 - Acc:97.30%
538
Train Epoch 50/50 - 

Train Epoch 50/50 - Loss:0.5116 - Acc:97.20%
687
Train Epoch 50/50 - Loss:0.5116 - Acc:97.20%
688
Train Epoch 50/50 - Loss:0.5116 - Acc:97.21%
689
Train Epoch 50/50 - Loss:0.5116 - Acc:97.21%
690
Train Epoch 50/50 - Loss:0.5115 - Acc:97.21%
691
Train Epoch 50/50 - Loss:0.5116 - Acc:97.22%
692
Train Epoch 50/50 - Loss:0.5115 - Acc:97.22%
693
Train Epoch 50/50 - Loss:0.5114 - Acc:97.23%
694
Train Epoch 50/50 - Loss:0.5115 - Acc:97.23%
695
Train Epoch 50/50 - Loss:0.5114 - Acc:97.23%
696
Train Epoch 50/50 - Loss:0.5114 - Acc:97.24%
697
Train Epoch 50/50 - Loss:0.5114 - Acc:97.24%
698
Train Epoch 50/50 - Loss:0.5113 - Acc:97.25%
699
Train Epoch 50/50 - Loss:0.5113 - Acc:97.25%
700
Train Epoch 50/50 - Loss:0.5112 - Acc:97.25%
701
Train Epoch 50/50 - Loss:0.5112 - Acc:97.26%
702
Train Epoch 50/50 - Loss:0.5111 - Acc:97.26%
703
Train Epoch 50/50 - Loss:0.5110 - Acc:97.27%
704
Train Epoch 50/50 - Loss:0.5115 - Acc:97.23%
705
Train Epoch 50/50 - Loss:0.5116 - Acc:97.24%
706
Train Epoch 50/50 - 

Train Epoch 50/50 - Loss:0.5115 - Acc:97.34%
855
Train Epoch 50/50 - Loss:0.5114 - Acc:97.34%
856
Train Epoch 50/50 - Loss:0.5113 - Acc:97.35%
857
Train Epoch 50/50 - Loss:0.5121 - Acc:97.33%
858
Train Epoch 50/50 - Loss:0.5120 - Acc:97.34%
859
Train Epoch 50/50 - Loss:0.5120 - Acc:97.34%
860
Train Epoch 50/50 - Loss:0.5120 - Acc:97.33%
861
Train Epoch 50/50 - Loss:0.5120 - Acc:97.33%
862
Train Epoch 50/50 - Loss:0.5121 - Acc:97.32%
863
Train Epoch 50/50 - Loss:0.5120 - Acc:97.32%
864
Train Epoch 50/50 - Loss:0.5119 - Acc:97.33%
865
Train Epoch 50/50 - Loss:0.5119 - Acc:97.33%
866
Train Epoch 50/50 - Loss:0.5119 - Acc:97.33%
867
Train Epoch 50/50 - Loss:0.5118 - Acc:97.34%
868
Train Epoch 50/50 - Loss:0.5117 - Acc:97.34%
869
Train Epoch 50/50 - Loss:0.5117 - Acc:97.34%
870
Train Epoch 50/50 - Loss:0.5116 - Acc:97.35%
871
Train Epoch 50/50 - Loss:0.5116 - Acc:97.35%
872
Train Epoch 50/50 - Loss:0.5115 - Acc:97.35%
873
Train Epoch 50/50 - Loss:0.5116 - Acc:97.35%
874
Train Epoch 50/50 - 

Train Epoch 50/50 - Loss:0.5116 - Acc:97.26%
1022
Train Epoch 50/50 - Loss:0.5116 - Acc:97.26%
1023
Train Epoch 50/50 - Loss:0.5115 - Acc:97.27%
1024
Train Epoch 50/50 - Loss:0.5115 - Acc:97.27%
1025
Train Epoch 50/50 - Loss:0.5114 - Acc:97.27%
1026
Train Epoch 50/50 - Loss:0.5114 - Acc:97.27%
1027
Train Epoch 50/50 - Loss:0.5113 - Acc:97.28%
1028
Train Epoch 50/50 - Loss:0.5113 - Acc:97.28%
1029
Train Epoch 50/50 - Loss:0.5112 - Acc:97.28%
1030
Train Epoch 50/50 - Loss:0.5112 - Acc:97.28%
1031
Train Epoch 50/50 - Loss:0.5112 - Acc:97.29%
1032
Train Epoch 50/50 - Loss:0.5113 - Acc:97.27%
1033
Train Epoch 50/50 - Loss:0.5113 - Acc:97.27%
1034
Train Epoch 50/50 - Loss:0.5112 - Acc:97.27%
1035
Train Epoch 50/50 - Loss:0.5112 - Acc:97.27%
1036
Train Epoch 50/50 - Loss:0.5112 - Acc:97.28%
1037
Train Epoch 50/50 - Loss:0.5112 - Acc:97.28%
1038
Train Epoch 50/50 - Loss:0.5112 - Acc:97.28%
1039
Train Epoch 50/50 - Loss:0.5112 - Acc:97.28%
1040
Train Epoch 50/50 - Loss:0.5112 - Acc:97.29%
1041


Train Epoch 50/50 - Loss:0.5108 - Acc:97.31%
1186
Train Epoch 50/50 - Loss:0.5110 - Acc:97.29%
1187
Train Epoch 50/50 - Loss:0.5110 - Acc:97.30%
1188
Train Epoch 50/50 - Loss:0.5109 - Acc:97.30%
1189
Train Epoch 50/50 - Loss:0.5108 - Acc:97.30%
1190
Train Epoch 50/50 - Loss:0.5109 - Acc:97.29%
1191
Train Epoch 50/50 - Loss:0.5109 - Acc:97.29%
1192
Train Epoch 50/50 - Loss:0.5108 - Acc:97.30%
1193
Train Epoch 50/50 - Loss:0.5108 - Acc:97.30%
1194
Train Epoch 50/50 - Loss:0.5108 - Acc:97.30%
1195
Train Epoch 50/50 - Loss:0.5108 - Acc:97.30%
1196
Train Epoch 50/50 - Loss:0.5107 - Acc:97.31%
1197
Train Epoch 50/50 - Loss:0.5107 - Acc:97.31%
1198
Train Epoch 50/50 - Loss:0.5107 - Acc:97.31%
1199
Train Epoch 50/50 - Loss:0.5110 - Acc:97.29%
1200
Train Epoch 50/50 - Loss:0.5110 - Acc:97.29%
1201
Train Epoch 50/50 - Loss:0.5110 - Acc:97.30%
1202
Train Epoch 50/50 - Loss:0.5110 - Acc:97.30%
1203
Train Epoch 50/50 - Loss:0.5109 - Acc:97.30%
1204
Train Epoch 50/50 - Loss:0.5109 - Acc:97.30%
1205


In [4]:
def testWithTask(net, recall_ids):
    net.eval()
    with torch.no_grad():
        # obtain feature vectors for all data
        for key in eval_dict.keys():
            eval_dict[key]['features'] = []
            imgList=[]
            # for inputs, labels in tqdm(eval_dict[key]['data_loader'], desc='processing {} data'.format(key)):
            print('processing {} data'.format(key))
            for batch_idx, (inputs, labels, imgs) in enumerate(eval_dict[key]['data_loader']):
                inputs, labels = inputs.cuda(), labels.cuda()
                features, classes = net(inputs)
                eval_dict[key]['features'].append(features)
                imgList+=imgs
            eval_dict[key]['features'] = torch.cat(eval_dict[key]['features'], dim=0)

        # compute recall metric
        if data_name == 'isc':
            acc_list = recallWithTask(eval_dict['test']['features'], test_data_set.label_list, recall_ids,imgList,
                              eval_dict['gallery']['features'], gallery_data_set.label_list)
        else:
            acc_list = recallWithTask(eval_dict['test']['features'], test_data_set.label_list, recall_ids,imgList)
    
    desc = 'Test Epoch {}/{} '.format(epoch, num_epochs)
    for index, rank_id in enumerate(recall_ids):
        desc += 'R@{}:{:.2f}%'.format(rank_id, acc_list[index] * 100)
        resultsWithC['test_recall@{}'.format(rank_id)].append(acc_list[index] * 100)
    print(desc)
    return acc_list[0]


In [10]:
def recallWithTask(feature_vectors, feature_labels, rank,test_img_list, gallery_vectors=None, gallery_labels=None):
    num_features = len(feature_labels)
    feature_labels = torch.tensor(feature_labels, device=feature_vectors.device)
    gallery_vectors = feature_vectors if gallery_vectors is None else gallery_vectors

    dist_matrix = torch.cdist(feature_vectors.unsqueeze(0), gallery_vectors.unsqueeze(0)).squeeze(0)
    
#     for i in range(len(test_img_list)):
#         for j in range(len(test_img_list)):
#             index1=test_img_list[i].rfind('\\')
#             index2=test_img_list[j].rfind('\\')
#             if test_img_list[i][index1+4:index1+7] == test_img_list[j][index2+4:index2+7] and i!=j :
#                 dist_matrix[i][j]=float('inf')
    
    
    if gallery_labels is None:
        dist_matrix.fill_diagonal_(float('inf'))
        gallery_labels = feature_labels
    else:
        gallery_labels = torch.tensor(gallery_labels, device=feature_vectors.device)

    idx = dist_matrix.topk(k=rank[-1], dim=-1, largest=False)[1]
    acc_list = []
    for r in rank:
        correct = (gallery_labels[idx[:, 0:r]] == feature_labels.unsqueeze(dim=-1)).any(dim=-1).float()
        acc_list.append((torch.sum(correct) / num_features).item())
    return acc_list


In [6]:
test_path="D:\\original_images_5\\few-person\\for colab\\different test"
class_test_name, test_img_list = get_data_list(test_path)


test_data_set = SingleData(class_test_name, test_img_list, train_transform)
test_data_loader = DataLoader(test_data_set, batch_size, shuffle=False, num_workers=8)
eval_dict = {'test': {'data_loader': test_data_loader}}

0
['s1', 's2', 's3']


In [12]:
resultsWithC={}
for recall_id in recalls:
    resultsWithC['test_recall@{}'.format(recall_id)] = []

In [9]:
rank2 = testWithTask(model, recalls)
print(resultsWithC)

processing test data
Test Epoch 50/50 R@1:35.98%R@2:52.13%R@4:70.27%R@8:85.06%
{'test_recall@1': [35.975608229637146], 'test_recall@2': [52.13414430618286], 'test_recall@4': [70.27438879013062], 'test_recall@8': [85.06097197532654]}


# easier

In [11]:
rank2 = testWithTask(model, recalls)
print(resultsWithC)

processing test data
Test Epoch 50/50 R@1:46.80%R@2:69.21%R@4:85.82%R@8:95.27%
{'test_recall@1': [35.975608229637146, 46.79877758026123], 'test_recall@2': [52.13414430618286, 69.20731663703918], 'test_recall@4': [70.27438879013062, 85.82316637039185], 'test_recall@8': [85.06097197532654, 95.27438879013062]}
